In [46]:
import nltk
from tqdm import tqdm
import xlrd
import pandas as pd
import random
from textblob import TextBlob
import numpy as np
import IPython
import re
from nltk.corpus import stopwords
import json
from gensim.models import Word2Vec
import time
from nltk import sent_tokenize
from senticnet.senticnet import SenticNet

# import matplotlib.pyplot as plt


In [90]:
adj = ['JJ','JJR','JJS']
adv = ['RB','RBR','RBS']
vb = ['VB','VBD','VBG','VBN','VBP','VBZ']
nn = ['NN','NNS']

sn = SenticNet()

def review_to_words(review_text): 
    if '(Reuters) -' in review_text:
        review_text = review_text.split('(Reuters) -')[1]
    if '*' in review_text:
        review_text = review_text.split('*')[1]
    letters_only = re.sub("[^a-zA-Z]", " ", review_text) 
    words = letters_only.split()                             
    _stopwords = set(stopwords.words("english"))
    _stopwords = nltk.corpus.stopwords.words('english')
    _stopwords.append('would')
    _stopwords.append('kmh')
    _stopwords.append('mph')
    _stopwords.append('  ')
    _stopwords.append('Reuters')
    _stopwords.append('reuters')
    # _stopwords = []
    meaningful_words = [w for w in words if w not in _stopwords]
    return meaningful_words

# d = enchant.Dict("en_US")
# import spacy
# nlp = spacy.load('en')
# def stem_and_check(word):
#     word = nlp(word)
#     return word[0].lemma_
    # word = inf.singularize(word)
    # word = nltk.PorterStemmer().stem(word)
    # if d.check(word):
    #    return word
    # suggest_words = d.suggest(word)
    # if len(suggest_words) == 0:
    #    return word
    # return suggest_words[0]

def my_read(path):
    file = open(path)
    words = []
    for line in file.readlines():
        words.append(line.strip())
    return words

    
def output_cloud(count,name):
    # 云图
    text = '' 
    for key,value in count.items():
        text += (key+' ') * (value)
    wc = WordCloud(
        width=1000,
        height=600,
        max_font_size=100,      #字体大小
        min_font_size=10,
        collocations=False, 
        max_words=1000
    )
    wc.generate(text)
    wc.to_file(name+'.png') #图片保存



def vote(results,datas):
    if len(datas) != len(results):
        raise("vote error")
    vote_dict = {}
    date_set = set([data['date'] for data in datas])
    company_set = set([data['company'] for data in datas])
    for company in company_set:
        vote_dict[company] = {}
        for date in date_set:
            vote_dict[company][date] = set()
    for idx in range(0,len(datas)):
        date = datas[idx]['date']
        company = datas[idx]['company']         
        vote_dict[company][date].add(idx)
        
    new_results = []
    print('voting')
    for i in range(0,len(results)):
        count = 0
        company = datas[i]['company']
        date = datas[i]['date']
        for idx in vote_dict[company][date]:
            count += results[idx]
        if count < 0:  
            new_results.append(np.float64(-1))
        else:
            new_results.append(np.float64(1))
    return np.array(new_results)

def accuracy(y,y2):
    if len(y) != len(y2):
        raise Exception("error")
    count = 0
    for i in range(0,len(y)):
        if y[i] == y2[i]:
            count += 1
    return count/len(y2)

# concept_info = sn.concept('love')
# polarity_value = sn.polarity_value('love')
# polarity_intense = sn.polarity_intense('love')
# moodtags = sn.moodtags('love')
# semantics = sn.semantics('love')
# sentics = sn.sentics('love') 
 
def sentiment_score(text):
    t = TextBlob(text)
    score = t.sentiment.polarity
    return score
    # tokens = nltk.word_tokenize(text)
    # pos_tags = nltk.pos_tag(tokens)
    # score = 0
    # count = 0
    # for word,tag in pos_tags:
    #   if word in sn.data.keys():
    #    score += float(sn.polarity_intense(word))
    #    count += 1
    #    # print(word,sn.polarity_intense(word))
    # if count == 0: #mid
    #   return -1 
    # return score/count
    
def load_data(path):
    workbook = xlrd.open_workbook(path)
    worksheet = workbook.sheet_by_index(0)
    contents = worksheet.col_values(1)
    companies = worksheet.col_values(2)
    prices = worksheet.col_values(3)
    dates = worksheet.col_values(4)
    datas = []
    for i in tqdm(range(0,len(contents))):
    # if '*' not in contents[i]:
        # if companies[i] != 'Apple Inc.':
        #     continue
        price_list = json.loads(prices[i])   
        if price_list[2] == price_list[1]:
            continue
        data = {}
        data['content'] = contents[i]
        sents = sent_tokenize(data['content'])
        data['tokens'] = []
        data['tags'] = []
        for sent in sents:
            token = review_to_words(sent) # 去停用词会影响词性标注吗？？
            data['tokens'].append(token)
            data['tags'].append(nltk.pos_tag(token))
        data['company'] = companies[i]
        data['rate'] = (price_list[2]-price_list[1])/price_list[1]
        data['date'] = dates[i]
        datas.append(data)

    return datas

In [ ]:
def train_sent_dict(datas):
    count = {}

    POS = 0
    NEG = 0

    pos_count = 0
    neg_count = 0

    N = 0 #len of tokens
        
    for data in tqdm(datas):
        for tokens in data['tokens']: 
            N += len(tokens)
            rate = data['rate'] # 选当天的股票变化判断涨跌，因为相关度当天的最高
            if rate>0:
                pos_count += 1
                POS += len(tokens)
                for token in tokens:
                    if len(token) < 3:
                        continue
                    if 'not' in tokens:
                        token = 'not_'+token
                    if token in count.keys():
                        count[token]['pos'] += 1
                        count[token]['pos_rate'] += rate
                    else:
                        count[token] = {'pos':1,'neg':0,'pos_rate':rate,'neg_rate':0} 

            if rate<0:
                neg_count += 1
                NEG += len(tokens)
                for token in tokens:
                    if len(token) < 3:
                        continue
                    if 'not' in tokens:
                        token = 'not_'+token
                    if token in count.keys():
                        count[token]['neg'] += 1
                        count[token]['neg_rate'] -= rate
                    else:
                        count[token] = {'pos':0,'neg':1,'pos_rate':0,'neg_rate':-rate}
                        ## freq
    copy = count.copy()
    sent_words = [] # PD>0.3情感值

    freq_pos = pos_count/len(datas) 
    freq_neg = neg_count/len(datas)

    # DS sent and PMI sent
    for word,value in tqdm(copy.items()):
        if value['pos']+value['neg']<len(datas)/100:
            del count[word]
            continue
        freq_w_pos = value['pos']/len(datas)
        freq_w_neg = value['neg']/len(datas)
        freq_w = (value['pos']+value['neg'])/len(datas)
        if freq_w_pos*N == 0:
            PMI_w_pos = 0
        else:
            PMI_w_pos = np.log2(freq_w_pos*N/freq_w*freq_pos)
        if freq_w_neg*N == 0:
            PMI_w_neg = 0
        else:
            PMI_w_neg = np.log2(freq_w_neg*N/freq_w*freq_neg)
        count[word]['PMI_sent'] = PMI_w_pos - PMI_w_neg

        pos = value['pos']/len(datas)
        neg = value['neg']/len(datas)
        value['PD'] = (pos-neg)/(pos+neg) # polarity difference
        if abs(value['PD']) > 0.3 and nltk.pos_tag([word])[0][1] in adj+adv:  
            sent_words.append(word)
        count[word]['sent'] = value['PD']*value['PD'] * np.sign(value['PD'])

        pos_rate = value['pos_rate']/len(datas)
        neg_rate = value['neg_rate']/len(datas)
        value['PD_rate'] = (pos_rate-neg_rate)/(pos_rate+neg_rate) # polarity difference
        count[word]['sent_rate'] = value['PD_rate']*value['PD_rate'] * np.sign(value['PD_rate'])
    return count


In [42]:
def news2vector(datas,count,bl_sent):
    for data in tqdm(datas):
        idx = datas.index(data)
        tokens = data['tokens']
        datas[idx]['DsVector'] = [0,0,0,0]
        datas[idx]['DsVector_rate'] = [0,0,0,0]
        datas[idx]['SnVector'] = [0,0,0,0]
        datas[idx]['BlVector'] = [0,0,0,0]
        datas[idx]['PmiVector'] = [0,0,0,0]
        datas[idx]['ContextVector'] = [0,0,0,0]
        
        # for f in [token for token in tokens if token in sentiment_feature.keys()]:
        #     for w in sentiment_feature[f].keys():
        #         if w in tokens:
        #             if abs(tokens.index(f)-tokens.index(w))<3 and ',' not in data['content'][min(data['content'].index(f),data['content'].index(w)):max(data['content'].index(f),data['content'].index(w))]:
        #                 if tags[tokens.index(f)][1] in adj:
        #                     if f in count.keys():
        #                         datas[idx]['ContextVector'][0] += count[f]['sent']
        #                 elif tags[tokens.index(f)][1] in adv:
        #                     if f in count.keys():
        #                         datas[idx]['ContextVector'][1] += count[f]['sent']
        #                 if tags[tokens.index(w)][1] in nn:
        #                     if w in count.keys():
        #                         datas[idx]['ContextVector'][2] = count[w]['sent']
        #                 elif tags[tokens.index(w)][1] in vb:
        #                     if w in count.keys():
        #                         datas[idx]['ContextVector'][3] = count[w]['sent']
        #                 # print(sentiment_feature[f][w]['sent'])
        for tags in data['tags']:
            for word,tag in tags:
                if tag in adj:
                    if word in count.keys():
                        datas[idx]['DsVector'][0] += count[word]['sent']
                        datas[idx]['DsVector_rate'][0] += count[word]['sent_rate']
                        datas[idx]['PmiVector'][0] += count[word]['PMI_sent']
                    if word in sn.data.keys():
                        datas[idx]['SnVector'][0] += float(sn.polarity_intense(word))
                    if word in bl_sent.keys():
                        datas[idx]['BlVector'][0] += bl_sent[word]
                elif tag in adv:
                    if word in count.keys():
                        datas[idx]['DsVector'][1] += count[word]['sent']
                        datas[idx]['DsVector_rate'][1] += count[word]['sent_rate']
                        datas[idx]['PmiVector'][1] += count[word]['PMI_sent']
                    if word in sn.data.keys():
                        datas[idx]['SnVector'][1] += float(sn.polarity_intense(word))
                    if word in bl_sent.keys():
                        datas[idx]['BlVector'][1] += bl_sent[word]  
                elif tag in nn:
                    if word in count.keys():
                        datas[idx]['DsVector'][2] = count[word]['sent']
                        datas[idx]['DsVector_rate'][2] += count[word]['sent_rate']
                        datas[idx]['PmiVector'][2] += count[word]['PMI_sent']
                    if word in sn.data.keys():
                        datas[idx]['SnVector'][2] += float(sn.polarity_intense(word))
                    if word in bl_sent.keys():
                        datas[idx]['BlVector'][2] += bl_sent[word]
                elif tag in vb:
                    if word in count.keys():
                        datas[idx]['DsVector'][3] = count[word]['sent']
                        datas[idx]['DsVector_rate'][3] += count[word]['sent_rate']
                        datas[idx]['PmiVector'][3] += count[word]['PMI_sent']
                    if word in sn.data.keys():
                        datas[idx]['SnVector'][3] += float(sn.polarity_intense(word))
                    if word in bl_sent.keys():
                        datas[idx]['BlVector'][3] += bl_sent[word]
        # datas[idx]['DsVector'] = [adv_score,adv_score,noun_score,verb_score]


In [43]:
import pickle
datas = pickle.load(open('/home/stocksentiment/datas.pkl','rb'))
count = pickle.load(open('/home/stocksentiment/sent_dict.pkl', 'rb'))
print('load finish')

load finish


In [101]:
path = r'~/Dynamic-Financial-News-Collection-and-Analysis/labeled_data.xls'

# datas = load_data(path)
# count = train_sent_dict(datas)

# import pickle
# output = open('sent_dict.pkl', 'wb')
# input = open('sent_dict.pkl', 'rb')
# s = pickle.dump(count, output)
# output.close()
# clf2 = pickle.load(input)
# input.close()
# print clf2.predict(X[0:1])

In [102]:
## 新闻情感值和股价的相关度
workbook = xlrd.open_workbook(path)
worksheet = workbook.sheet_by_index(0)
contents = worksheet.col_values(1)
companies = worksheet.col_values(2)
prices = worksheet.col_values(3)
dates = worksheet.col_values(4)

In [103]:
rates = []
score_list = []

for i in tqdm(range(0,len(contents))):
    rate = []
    price_list = json.loads(prices[i])
    for idx in range(0,6):
        rate.append((price_list[idx+1]-price_list[idx])/price_list[idx])
    rates.append(rate)
    score_list.append(sentiment_score(contents[i]))
    
## 合并一天新闻
# for i in tqdm(range(0,len(contents))):
#     rate = []
#     price_list = json.loads(prices[i])
#     for idx in range(0,6):
#       rate.append((price_list[idx+1]-price_list[idx])/price_list[idx])
#     if rate in rates:
#         idx = rates.index(rate)
#         score_list[idx] += sentiment_score(contents[i])
#         continue
#     rates.append(rate)
#     score_list.append(sentiment_score(contents[i]))

# 情感极性与六天内（包括）新闻涨跌比率的相关度
fiveday_rate_list = []
for i in range(0,6):
    rate = [x[i] for x in rates]
    data = {
        'scores':score_list,
        'rates':rate
        }

    df = pd.DataFrame(data)
   # print(df)
    print(df.corr("kendall"))
















  0%|          | 0/366411 [00:00<?, ?it/s]














  0%|          | 1/366411 [00:00<22:12:28,  4.58it/s]














  0%|          | 28/366411 [00:00<15:39:28,  6.50it/s]














  0%|          | 55/366411 [00:00<11:04:33,  9.19it/s]














  0%|          | 80/366411 [00:00<7:52:43, 12.92it/s] 














  0%|          | 104/366411 [00:00<5:38:31, 18.03it/s]














  0%|          | 131/366411 [00:00<4:03:56, 25.02it/s]














  0%|          | 157/366411 [00:00<2:57:50, 34.32it/s]














  0%|          | 185/366411 [00:00<2:11:03, 46.57it/s]














  0%|          | 213/366411 [00:01<1:38:17, 62.10it/s]














  0%|          | 239/366411 [00:01<1:16:36, 79.67it/s]














  0%|          | 264/366411 [00:01<1:01:21, 99.45it/s]














  0%|          | 289/366411 [00:01<50:33, 120.68it/s] 














  0%|          | 314/366411 [00:01<43:59, 138.71it/s]














  0%|          | 339/366411 [00:0

  0%|          | 1829/366411 [00:07<27:40, 219.56it/s]














  1%|          | 1855/366411 [00:08<26:25, 229.88it/s]














  1%|          | 1879/366411 [00:08<26:06, 232.70it/s]














  1%|          | 1903/366411 [00:08<26:39, 227.95it/s]














  1%|          | 1927/366411 [00:08<26:55, 225.60it/s]














  1%|          | 1950/366411 [00:08<30:46, 197.43it/s]














  1%|          | 1971/366411 [00:08<32:42, 185.66it/s]














  1%|          | 1995/366411 [00:08<30:43, 197.64it/s]














  1%|          | 2017/366411 [00:08<29:47, 203.82it/s]














  1%|          | 2041/366411 [00:08<28:46, 211.04it/s]














  1%|          | 2063/366411 [00:09<28:50, 210.60it/s]














  1%|          | 2089/366411 [00:09<27:20, 222.13it/s]














  1%|          | 2116/366411 [00:09<26:09, 232.07it/s]














  1%|          | 2143/366411 [00:09<25:18, 239.85it/s]














  1%|          | 2168/366411 [00:0

  1%|          | 3455/366411 [00:16<36:21, 166.35it/s]














  1%|          | 3479/366411 [00:16<33:06, 182.74it/s]














  1%|          | 3507/366411 [00:16<29:41, 203.76it/s]














  1%|          | 3530/366411 [00:16<29:08, 207.58it/s]














  1%|          | 3553/366411 [00:16<28:31, 212.02it/s]














  1%|          | 3576/366411 [00:16<28:09, 214.76it/s]














  1%|          | 3599/366411 [00:16<28:16, 213.92it/s]














  1%|          | 3625/366411 [00:16<26:57, 224.31it/s]














  1%|          | 3651/366411 [00:17<26:04, 231.83it/s]














  1%|          | 3675/366411 [00:17<26:39, 226.72it/s]














  1%|          | 3698/366411 [00:17<27:11, 222.28it/s]














  1%|          | 3722/366411 [00:17<26:45, 225.87it/s]














  1%|          | 3745/366411 [00:17<26:58, 224.06it/s]














  1%|          | 3771/366411 [00:17<26:04, 231.73it/s]














  1%|          | 3795/366411 [00:1

  1%|▏         | 5160/366411 [00:24<34:51, 172.75it/s]














  1%|▏         | 5179/366411 [00:24<40:45, 147.73it/s]














  1%|▏         | 5198/366411 [00:24<39:18, 153.13it/s]














  1%|▏         | 5215/366411 [00:24<39:50, 151.09it/s]














  1%|▏         | 5238/366411 [00:24<35:50, 167.94it/s]














  1%|▏         | 5258/366411 [00:24<36:11, 166.34it/s]














  1%|▏         | 5276/366411 [00:25<47:15, 127.37it/s]














  1%|▏         | 5291/366411 [00:25<47:35, 126.47it/s]














  1%|▏         | 5308/366411 [00:25<44:07, 136.37it/s]














  1%|▏         | 5325/366411 [00:25<42:00, 143.27it/s]














  1%|▏         | 5341/366411 [00:25<40:57, 146.91it/s]














  1%|▏         | 5357/366411 [00:25<50:07, 120.03it/s]














  1%|▏         | 5380/366411 [00:25<43:23, 138.68it/s]














  1%|▏         | 5399/366411 [00:26<39:53, 150.84it/s]














  1%|▏         | 5421/366411 [00:2

  2%|▏         | 6580/366411 [00:32<41:14, 145.39it/s]














  2%|▏         | 6600/366411 [00:33<38:04, 157.50it/s]














  2%|▏         | 6622/366411 [00:33<35:26, 169.17it/s]














  2%|▏         | 6641/366411 [00:33<35:26, 169.16it/s]














  2%|▏         | 6666/366411 [00:33<32:13, 186.08it/s]














  2%|▏         | 6687/366411 [00:33<37:42, 158.96it/s]














  2%|▏         | 6711/366411 [00:33<33:55, 176.75it/s]














  2%|▏         | 6731/366411 [00:33<50:58, 117.58it/s]














  2%|▏         | 6747/366411 [00:34<46:56, 127.68it/s]














  2%|▏         | 6772/366411 [00:34<40:05, 149.48it/s]














  2%|▏         | 6797/366411 [00:34<35:28, 168.96it/s]














  2%|▏         | 6822/366411 [00:34<32:01, 187.15it/s]














  2%|▏         | 6851/366411 [00:34<28:39, 209.07it/s]














  2%|▏         | 6875/366411 [00:34<27:53, 214.78it/s]














  2%|▏         | 6899/366411 [00:3

...

 98%|█████████▊| 357411/366411 [28:58<00:27, 323.67it/s]














 98%|█████████▊| 357448/366411 [28:58<00:26, 333.10it/s]














 98%|█████████▊| 357485/366411 [28:58<00:26, 342.44it/s]














 98%|█████████▊| 357522/366411 [28:58<00:25, 349.39it/s]














 98%|█████████▊| 357558/366411 [28:58<00:25, 343.89it/s]














 98%|█████████▊| 357605/366411 [28:58<00:23, 373.92it/s]














 98%|█████████▊| 357646/366411 [28:58<00:22, 383.92it/s]














 98%|█████████▊| 357686/366411 [28:58<00:22, 382.54it/s]














 98%|█████████▊| 357725/366411 [28:58<00:23, 363.23it/s]














 98%|█████████▊| 357762/366411 [28:59<00:25, 336.80it/s]














 98%|█████████▊| 357802/366411 [28:59<00:24, 349.22it/s]














 98%|█████████▊| 357838/366411 [28:59<00:26, 328.30it/s]














 98%|█████████▊| 357872/366411 [28:59<00:25, 328.66it/s]














 98%|█████████▊| 357915/366411 [28:59<00:24, 352.19it/s]














 98%|█

 98%|█████████▊| 360082/366411 [29:05<00:19, 318.27it/s]














 98%|█████████▊| 360122/366411 [29:05<00:18, 338.77it/s]














 98%|█████████▊| 360163/366411 [29:05<00:17, 354.75it/s]














 98%|█████████▊| 360207/366411 [29:05<00:16, 376.23it/s]














 98%|█████████▊| 360246/366411 [29:06<00:16, 374.76it/s]














 98%|█████████▊| 360286/366411 [29:06<00:16, 379.44it/s]














 98%|█████████▊| 360325/366411 [29:06<00:16, 378.73it/s]














 98%|█████████▊| 360364/366411 [29:06<00:17, 349.30it/s]














 98%|█████████▊| 360405/366411 [29:06<00:16, 363.37it/s]














 98%|█████████▊| 360443/366411 [29:06<00:16, 366.37it/s]














 98%|█████████▊| 360486/366411 [29:06<00:15, 382.67it/s]














 98%|█████████▊| 360527/366411 [29:06<00:15, 389.49it/s]














 98%|█████████▊| 360567/366411 [29:06<00:16, 355.57it/s]














 98%|█████████▊| 360604/366411 [29:07<00:17, 337.32it/s]














 98%|█

 99%|█████████▉| 362894/366411 [29:13<00:10, 348.08it/s]














 99%|█████████▉| 362936/366411 [29:13<00:09, 366.80it/s]














 99%|█████████▉| 362974/366411 [29:13<00:09, 356.60it/s]














 99%|█████████▉| 363020/366411 [29:13<00:09, 376.56it/s]














 99%|█████████▉| 363059/366411 [29:13<00:08, 377.51it/s]














 99%|█████████▉| 363098/366411 [29:13<00:09, 363.55it/s]














 99%|█████████▉| 363135/366411 [29:13<00:09, 338.09it/s]














 99%|█████████▉| 363170/366411 [29:14<00:10, 319.93it/s]














 99%|█████████▉| 363203/366411 [29:14<00:10, 305.89it/s]














 99%|█████████▉| 363238/366411 [29:14<00:09, 317.80it/s]














 99%|█████████▉| 363278/366411 [29:14<00:09, 338.14it/s]














 99%|█████████▉| 363313/366411 [29:14<00:09, 337.96it/s]














 99%|█████████▉| 363353/366411 [29:14<00:08, 353.99it/s]














 99%|█████████▉| 363396/366411 [29:14<00:08, 372.31it/s]














 99%|█

100%|█████████▉| 365627/366411 [29:20<00:02, 352.83it/s]














100%|█████████▉| 365664/366411 [29:21<00:02, 344.61it/s]














100%|█████████▉| 365700/366411 [29:21<00:02, 331.84it/s]














100%|█████████▉| 365734/366411 [29:21<00:02, 311.85it/s]














100%|█████████▉| 365768/366411 [29:21<00:02, 317.86it/s]














100%|█████████▉| 365801/366411 [29:21<00:01, 313.36it/s]














100%|█████████▉| 365846/366411 [29:21<00:01, 344.27it/s]














100%|█████████▉| 365889/366411 [29:21<00:01, 365.83it/s]














100%|█████████▉| 365927/366411 [29:21<00:01, 366.99it/s]














100%|█████████▉| 365965/366411 [29:21<00:01, 368.68it/s]














100%|█████████▉| 366003/366411 [29:22<00:01, 349.99it/s]














100%|█████████▉| 366042/366411 [29:22<00:01, 359.24it/s]














100%|█████████▉| 366079/366411 [29:22<00:00, 357.45it/s]














100%|█████████▉| 366119/366411 [29:22<00:00, 368.87it/s]














100%|█

           rates    scores
rates   1.000000  0.033801
scores  0.033801  1.000000
           rates    scores
rates   1.000000  0.002254
scores  0.002254  1.000000
           rates    scores
rates   1.000000  0.001984
scores  0.001984  1.000000
           rates    scores
rates   1.000000 -0.000839
scores -0.000839  1.000000
           rates    scores
rates   1.000000 -0.000409
scores -0.000409  1.000000
           rates    scores
rates   1.000000 -0.002007
scores -0.002007  1.000000


In [ ]:
# wordvec
tokens = []
for data in datas:
    for ts in data['tokens']:
        tokens.append(ts)
model = Word2Vec(sentences = tokens,min_count = 10)

In [ ]:
# subjective sent dictionary

bag_of_keywords = set(['rise','drop','fall','gain','surge','shrink','jump','slump','surge'])
stop = False
bok_size = 100
for i in range(10):
	new_words = []
	if stop:break
	for k in bag_of_keywords:
		if k in model.wv.vocab.keys():# wv = wordvector
			new_words.extend(model.most_similar(k))
for n in new_words:
	if n[0].islower() and len(n[0])>3 and n[0].isalpha():
		bag_of_keywords.add(n[0])
		if len(bag_of_keywords) == bok_size:
			stop = True
			break

'''fit():计算数据的参数，\mu（均值），\sigma（标准差），并存储在对象中（例如实例化的CountVectorizer()等）。
transform():将这些参数应用到数据集，进行标准化（尺度化）。'''

## Bag of keywords 统计词语的两个api
bag_of_keywords = np.array(list(bag_of_keywords))
bok_tfidf = TfidfVectorizer(lowercase = False, min_df = 1, vocabulary=bag_of_keywords)
X_bok_tfidf = bok_tfidf.fit_transform(sentences)
X_bok_tfidf = X_bok_tfidf.toarray()
bok_count = CountVectorizer(lowercase=False,min_df=1, vocabulary=bag_of_keywords)
X_bok_count = bok_count.fit_transform(sentences)
X_bok_count = X_bok_count.toarray()

## Category tag
category_tags = set(['published','presented','unveil','investment','bankrupt','acquisition','government'
                     'sue','lawsuit','highlights'])
stop = False
cate_size = 100

for _ in range(10):
    new_words = []
    if stop:break
    for k in category_tags:
        if k in model.wv.vocab.keys():
            new_words.extend(model.most_similar(k))
    for n in new_words:
        if n[0].islower() and len(n[0])>3 and n[0].isalpha():
            category_tags.add(n[0])
            if len(category_tags) == cate_size:
                stop = True
                break


category_tags = np.array(list(category_tags))

ct_count = CountVectorizer(lowercase = False, min_df = 1, vocabulary = category_tags)
X_ct_count = ct_count.fit_transform(sentences)
X_ct_count = X_ct_count.toarray()

ct_tfidf = TfidfVectorizer(lowercase = False, min_df = 1, vocabulary = category_tags)
X_ct_idf = ct_tfidf.fit_transform(sentences)
X_ct_idf = X_ct_idf.toarray()

full_tfidf = TfidfVectorizer(lowercase=False, min_df = 1,vocabulary=bag_of_keywords,use_idf=False)
X_full_tfidf = full_tfidf.fit_transform(sentences)
X_full_tfidf = X_full_tfidf.toarray()


num_classes = 2


In [18]:
## neg pos 词
# pos_words = {}
# neg_words = {}
# for word in sent_words:
#    if count[word]['sent'] > 0:
#       pos_words[word.lower()] = count[word]['pos']+count[word]['neg']
#    else:
#       neg_words[word.lower()] = count[word]['pos']+count[word]['neg']

# output_cloud(pos_words,'pos')
# output_cloud(neg_words,'neg')

# datas = load_data(path2019)

In [26]:
## neg pos 词
# pos_words = {}
# neg_words = {}
# for word in sent_words:
#    if count[word]['sent'] > 0:
#       pos_words[word.lower()] = count[word]['pos']+count[word]['neg']
#    else:
#       neg_words[word.lower()] = count[word]['pos']+count[word]['neg']

# output_cloud(pos_words,'pos')
# output_cloud(neg_words,'neg')

In [44]:
## 求于bl词典的覆盖率
bl_sent = {}
bl_pos = my_read('/home/stocksentiment/Dynamic-Financial-News-Collection-and-Analysis/sentiment_analysis/bl/positive.txt')  # 4783
bl_neg = my_read('/home/stocksentiment/Dynamic-Financial-News-Collection-and-Analysis/sentiment_analysis/bl/negative.txt')  # 2006


for word in bl_pos:
    bl_sent[word] = 1
for word in bl_pos:
    bl_sent[word] = -1
# pc = 0
# for word in pos_words:
#    if word in bl_pos:
#       pc += 1
# pos_accuracy = pc/len(pos_words)  # 0.2857142857142857

# nc = 0
# for word in neg_words:
#    if word in bl_neg:
#       nc += 1
# neg_accuracy = nc/len(neg_words)  # 0.18

In [28]:
## context sentiment dict
# sent_words = [word.lower() for word in sent_words]
# feature_words = {}
# sentiment_feature = {}

# for data in tqdm(datas):
#     for tags in data['tags']:
#         for word,tag in tags:
#             if tag not in nn or len(word)<3: # vb+nn
#                 continue
#             # word = stem_and_check(word)
#             if word not in feature_words.keys():
#                 feature_words[word] = 1
#             else:
#                 feature_words[word] += 1

# # avg_f = sum([item[1] for item in feature_words.items()])/len(feature_words.keys())
# res = sorted(feature_words.items(),key=lambda feature_words:feature_words[1],reverse=True)
# words = res[:400]
# # for word,value in tqdm(copy.items()):
# #     if value<avg_f+200:
# #         del feature_words[word]

# feature_words = [inf.singularize(word).lower() for word,freq in words]

# sf_len = 0
# for data in tqdm(datas):
#     rate = data['rate']
#     for tokens in data['tokens']:
#         token_dict = {}
#         for token in tokens:
#             token_dict[inf.singularize(token).lower()] = token
#         _tokens = [inf.singularize(token).lower() for token in tokens]

#         for w in list(set(sent_words).intersection(set(_tokens))):
#             for f in list(set(feature_words).intersection(set(_tokens))):
#                 if f != w:
#                     if abs(_tokens.index(w)-_tokens.index(f))<3 and ',' not in data['content'][min(data['content'].index(token_dict[f]),data['content'].index(token_dict[w])):max(data['content'].index(token_dict[f]),data['content'].index(token_dict[w]))]:
#                         sf_len += 1
#                         if f not in sentiment_feature.keys():
#                             sentiment_feature[f] = {}
#                             if rate > 0:
#                                 sentiment_feature[f][w] = {'pos':1,'neg':0}
#                             if rate < 0:
#                                 sentiment_feature[f][w] = {'pos':0,'neg':1}
#                         else:
#                             if w not in sentiment_feature[f].keys():
#                                 sentiment_feature[f][w] = {'pos':0,'neg':0}
#                             if rate > 0:
#                                 sentiment_feature[f][w]['pos'] += 1
#                             if rate < 0:
#                                 sentiment_feature[f][w]['neg'] += 1

# avg_sf = sf_len/len(sentiment_feature.keys())
# copy = sentiment_feature.copy()

# for f,v in tqdm(sentiment_feature.items()):
#     for w,value in v.items():
#         if value['pos']+value['neg']<avg_sf: #avg_sf
#             # print(f,w,value)
#             # del sentiment_feature[f][w]
#             sentiment_feature[f][w]['sent'] = 0
#             continue
#         pos = value['pos']/POS
#         neg = value['neg']/NEG
        
#         value['PD'] = (pos-neg)/(pos+neg) # polarity difference
#         sentiment_feature[f][w]['sent'] = value['PD'] * value['PD'] * np.sign(value['PD'])

# res = sorted(sentiment_feature.items(),key=lambda sentiment_feature:sentiment_feature[1]['sent'],reverse=False)

## company word
# company_pos = {}
# company_neg = {}
# for key,value in sentiment_feature.items():
#    if 'company' in key:
#       if sentiment_feature[key]['sent'] > 0:
#          company_pos[key.split('_')[0]] = sentiment_feature[key]['pos']
#       else:
#          company_neg[key.split('_')[0]] = sentiment_feature[key]['neg']

# output_cloud(company_pos,'company_pos')
# output_cloud(company_neg,'company_neg')


# for r in res[:30]:
#    print(r[0],r[1]['sent'],r[1]['pos']+r[1]['neg'])
#    print(' ')

# print(' ')
# print('========================')

# for r in res[-40:]:
#    print(r[0],r[1]['sent'],r[1]['pos'],r[1]['neg'])
#    print(' ')

# 展示
# pos_res = {}
# for r in res:
#     if r[1]['sent'] == 1.0:
#         pos_res[r[0]] = r[1]['pos']+r[1]['neg']
# pos_res = sorted(pos_res.items(),key=lambda pos_res:pos_res[1],reverse=True)
# for r in pos_res[:20]:
#     print(r[0],'1.0',r[1])
#     print(' ')

# print(' ')
# print('========================')
# print(' ')

# neg_res = {}
# for r in res:
#     if r[1]['sent'] == -1.0:
#         neg_res[r[0]] = r[1]['pos']+r[1]['neg']
# neg_res = sorted(neg_res.items(),key=lambda neg_res:neg_res[1],reverse=True)
# for r in neg_res[:20]:
#     print(r[0],'-1.0',r[1])
#     print(' ')
# for sf,value in sentiment_feature.items():
#    if value['pos']+value['neg'] > avg_sf:
#       print(sf,freq)

In [33]:
news2vector(datas,count,bl_sent)

100%|██████████| 363237/363237 [1:15:57<00:00, 27.32it/s] 


In [53]:
output = open('datas.pkl', 'wb')
pickle.dump(datas, output)
print('dump finish')

dump finish


{'BlVector': [0, 0, -4, 0],
 'ContextVector': [0, 0, 0, 0],
 'DsVector': [0.009382414055471773,
  0.003466796193975887,
  0.00011491759888645986,
  0.0008279551668078367],
 'DsVector_rate': [0.04473495161500582,
  0.01280244453155389,
  0.2797177700726252,
  0.10969579071672703],
 'PmiVector': [2.3897680592562054,
  0.9182778690101259,
  12.363459195184863,
  4.756092484475477],
 'SnVector': [-0.6450000000000007,
  -2.5869999999999997,
  12.297000000000002,
  1.055],
 'company': 'Ameriprise Financial',
 'content': 'NEW YORK  (Reuters) - H&R Block Inc will pay as much as $20.2 million to settle a New York lawsuit accusing it of fraudulently marketing retirement accounts that caused hundreds of thousands of mostly lower-income clients to lose money.    New York Attorney General Andrew Cuomo said the accord calls for the largest U.S. tax preparer to refund $11.4 million to $19.4 million of fees to customers nationwide who opened one of its Express IRAs, a type of individual retirement acc

In [88]:
vote_dict = {}
date_set = set([data['date'] for data in datas])
company_set = set([data['company'] for data in datas])
for company in company_set:
    vote_dict[company] = {}
    for date in date_set:
        vote_dict[company][date] = set()
for idx in range(0,len(datas)):
    date = datas[idx]['date']
    company = datas[idx]['company']         
    vote_dict[company][date].add(idx)

In [87]:
vote_dict['Harley-Davidson']

{'2017-10-13': set(),
 '2016-07-08': {302925, 302947, 302948, 303008},
 '2017-07-20': {338115, 338196, 338207},
 '2014-05-02': set(),
 '2013-09-12': set(),
 '2014-10-24': set(),
 '2016-05-31': set(),
 '2015-03-16': set(),
 '2012-05-08': set(),
 '2012-10-22': set(),
 '2017-11-24': set(),
 '2014-08-15': set(),
 '2017-01-05': set(),
 '2015-06-16': set(),
 '2014-04-10': set(),
 '2012-10-25': {146601},
 '2017-11-09': set(),
 '2016-11-15': set(),
 '2015-07-17': set(),
 '2011-09-13': set(),
 '2015-01-06': set(),
 '2015-04-15': set(),
 '2017-01-23': set(),
 '2010-01-07': set(),
 '2010-12-28': set(),
 '2017-06-28': set(),
 '2017-11-01': set(),
 '2012-02-09': set(),
 '2010-11-01': set(),
 '2014-02-18': set(),
 '2011-09-19': set(),
 '2015-10-08': set(),
 '2012-06-06': set(),
 '2013-10-02': set(),
 '2011-03-15': set(),
 '2012-06-20': set(),
 '2013-11-15': set(),
 '2012-05-23': set(),
 '2012-09-12': set(),
 '2013-03-06': set(),
 '2013-08-15': set(),
 '2015-09-10': set(),
 '2018-03-12': set(),
 '201

In [93]:
from sklearn.naive_bayes import GaussianNB
from sklearn.linear_model import LinearRegression
from sklearn import model_selection
from sklearn.model_selection import KFold
from sklearn.metrics import recall_score
from sklearn.metrics import precision_score
from sklearn.metrics import f1_score
from sklearn.metrics import mean_absolute_error
from sklearn.ensemble import RandomForestClassifier
from keras.utils import to_categorical
import matplotlib.pyplot as plt
# RandomForest
X1 = [data['DsVector'] for data in datas]
X2 = [data['SnVector'] for data in datas]
X3 = [data['BlVector'] for data in datas]
X4 = [data['PmiVector'] for data in datas]
X5 = [data['DsVector_rate'] for data in datas]

Xs = {'DsVector':X1,'SnVector':X2,'BlVector':X3,'PmiVector':X4,'DsVector_rate':X5}

Y = [np.sign(data['rate']) for data in datas]
for vectorname in Xs.keys():
    print(vectorname+'==============')
    X = Xs[vectorname]
    train_x,test_x,train_y,test_y = model_selection.train_test_split(X,Y,test_size=0.2,shuffle=False)

    clf = RandomForestClassifier(n_estimators=100, max_depth=2,random_state=0)

    clf.fit(np.array(train_x), np.array(train_y))

    predict_y = clf.predict(test_x)
    recall = recall_score(test_y,clf.predict(test_x),average = 'macro')
    precision = precision_score(test_y, clf.predict(test_x), average='macro')

    print('accuracy：',clf.score(np.array(test_x), np.array(test_y))) 
    print('recall：',recall)
    print('precision：',precision)
    print('f1_score',2*recall*precision/(recall+precision))

    vote_predict_y = vote(predict_y,datas[-len(test_x):])
    vote_recall = recall_score(test_y,vote_predict_y,average = 'macro')
    vote_precision = precision_score(test_y, vote_predict_y, average='macro')

    print('voting accuracy：',accuracy(vote_predict_y,test_y))
    print('voting recall：',vote_recall)
    print('voting precision：',vote_precision)
    print('voting f1_score',2*vote_recall*vote_precision/(vote_recall+vote_precision))
    print('')

BlVector==============
accuracy： 0.520881510846823
recall： 0.49998793967470384
precision： 0.4271112946520752
f1_score 0.4606853038336461
voting


/home/stocksentiment/.local/lib/python3.5/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


voting accuracy： 0.5208952758506772
voting recall： 0.5
voting precision： 0.2604476379253386
voting f1_score 0.34249253326092854

DsVector_rate==============
accuracy： 0.5214871710164078
recall： 0.5009265814680646
precision： 0.529247230471489
f1_score 0.5146976225543572
voting
voting accuracy： 0.5209365708622399
voting recall： 0.5001306865504281
voting precision： 0.5153190319154286
voting f1_score 0.507611271218312

SnVector==============
accuracy： 0.5206337407774474
recall： 0.49985037680282735
precision： 0.4860512225962932
f1_score 0.4928542298913098
voting
voting accuracy： 0.5206199757735932
voting recall： 0.4997530309590441
voting precision： 0.41038596104575886
voting f1_score 0.4506819940631131

DsVector==============
accuracy： 0.5242264067833939
recall： 0.5044502805334159
precision： 0.5429033077458991
f1_score 0.522970902968638
voting
voting accuracy： 0.5286036780090299
voting recall： 0.5084375949024605
voting precision： 0.6253113955024281
voting f1_score 0.5608504610545494

PmiVec

In [95]:
# GaussianNB
for vectorname in Xs.keys():
    print(vectorname+'==============')
    X = Xs[vectorname]
    train_x,test_x,train_y,test_y = model_selection.train_test_split(X,Y,test_size=0.2,shuffle=False)

    clf = GaussianNB()

    clf.fit(np.array(train_x), np.array(train_y))

    predict_y = clf.predict(test_x)
    recall = recall_score(test_y,clf.predict(test_x),average = 'macro')
    precision = precision_score(test_y, clf.predict(test_x), average='macro')

    print('accuracy：',clf.score(np.array(test_x), np.array(test_y))) 
    print('recall：',recall)
    print('precision：',precision)
    print('f1_score',2*recall*precision/(recall+precision))

    vote_predict_y = vote(predict_y,datas[-len(test_x):])
    vote_recall = recall_score(test_y,vote_predict_y,average = 'macro')
    vote_precision = precision_score(test_y, vote_predict_y, average='macro')

    print('voting accuracy：',accuracy(vote_predict_y,test_y))
    print('voting recall：',vote_recall)
    print('voting precision：',vote_precision)
    print('voting f1_score',2*vote_recall*vote_precision/(vote_recall+vote_precision))
    print('')

BlVector==============
accuracy： 0.5207851558198436
recall： 0.5010099241239496
precision： 0.5096778012454636
f1_score 0.5053066938877044
voting
voting accuracy： 0.5208677458429688
voting recall： 0.5003469866055271
voting precision： 0.5097657840922931
voting f1_score 0.5050124725558685

DsVector_rate==============
accuracy： 0.48305528025547845
recall： 0.502237350919005
precision： 0.5141714991563476
f1_score 0.5081343627324632
voting
voting accuracy： 0.4815273648276622
voting recall： 0.5014115204290613
voting precision： 0.5148850052055574
voting f1_score 0.5080589508953243

SnVector==============
accuracy： 0.5121269683955512
recall： 0.5002180083164723
precision： 0.5003223382921838
f1_score 0.5002701678648954
voting
voting accuracy： 0.5176880299526484
voting recall： 0.5011960585608762
voting precision： 0.5031678829563104
voting f1_score 0.5021800351597105

DsVector==============
accuracy： 0.48379859046360535
recall： 0.5024287581893708
precision： 0.5118029282265224
f1_score 0.5070725222069

In [25]:
# dnn
from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout
from keras.utils import to_categorical

Y = [np.sign(data['rate']) for data in datas]
for vectorname in Xs.keys():
    print(vectorname+'==============')
    X = Xs[vectorname]
    train_x,test_x,Y1,Y2 = model_selection.train_test_split(X,Y,test_size=0.2,shuffle=False)
    # train_x = [data['DsVector_rate'] for data in datas]
    # Y = [np.sign(data['rate']) for data in datas]
    # test_x = [data['DsVector_rate'] for data in datas2[2000:]]
    # Y2 = [np.sign(data['rate']) for data in datas2[2000:]]

    train_y = []
    for y in Y1:
        if y == 1:
            train_y.append(np.array([0,1]))
        else:    
            train_y.append(np.array([1,0]))

    test_y = []
    for y in Y2:
        if y == 1:
            test_y.append(np.array([0,1]))
        else:    
            test_y.append(np.array([1,0]))

    num_classes = 2
    
#     train_y = to_categorical(train_y,num_classes=num_classes)
#     test_y = to_categorical(test_y,num_classes=num_classes)
    nmodel = Sequential()
    nmodel.add(Dense(units=num_classes, activation = 'relu', input_dim = np.array(train_x).shape[1]))
    nmodel.add(Dropout(0.5))
    nmodel.add(Dense(2, activation = 'relu'))
    nmodel.add(Dropout(0.5))
    # dropout:https://blog.csdn.net/program_developer/article/details/80737724
    nmodel.add(Dense(2, activation = 'softmax'))
    nmodel.compile(loss = 'categorical_crossentropy',
                   optimizer = 'adam',
                   metrics = ['accuracy'])
    nmodel.fit(np.array(train_x),np.array(train_y),epochs=10, batch_size=5)
    print(nmodel.evaluate(np.array(test_x),np.array(test_y), batch_size=5))

BlVector==============
Epoch 1/10
290589/290589 [==============================] - 93s 319us/step - loss: 0.7055 - acc: 0.5070
Epoch 2/10
290589/290589 [==============================] - 93s 322us/step - loss: 0.6931 - acc: 0.5073
Epoch 3/10
290589/290589 [==============================] - 93s 321us/step - loss: 0.6931 - acc: 0.5072
Epoch 4/10
290589/290589 [==============================] - 92s 315us/step - loss: 0.6931 - acc: 0.5071
Epoch 5/10
290589/290589 [==============================] - 92s 316us/step - loss: 0.6931 - acc: 0.5080
Epoch 6/10
290589/290589 [==============================] - 92s 318us/step - loss: 0.6931 - acc: 0.5080
Epoch 7/10
290589/290589 [==============================] - 93s 319us/step - loss: 0.6931 - acc: 0.5074
Epoch 8/10
290589/290589 [==============================] - 93s 319us/step - loss: 0.6931 - acc: 0.5077
Epoch 9/10
290589/290589 [==============================] - 92s 318us/step - loss: 0.6931 - acc: 0.5073
Epoch 10/10
72648/72648 [================

In [40]:
# rnn
from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout
from keras.utils import to_categorical
from keras.layers import LSTM

for vectorname in Xs.keys():
    print(vectorname+'==============')
    X1 = Xs[vectorname]
    X = []
    for idx in tqdm(range(0,len(X1))):
        X.append([[X1[idx],1]])
    X = np.array(X)
    X = np.concatenate(X, axis=0)
    print(X.shape)
    train_x,test_x,Y1,Y2 = model_selection.train_test_split(X,Y,test_size=0.2,shuffle=False)

    train_y = []
    for y in Y1:
        if y == 1:
            train_y.append(np.array([0,1]))
        else:    
            train_y.append(np.array([1,0]))

    test_y = []
    for y in Y2:
        if y == 1:
            test_y.append(np.array([0,1]))
        else:    
            test_y.append(np.array([1,0]))

    num_classes = 2
    neurons = 2                 
    activation_function = 'tanh'  
    loss = 'mse'                  
    optimizer="adam"              
    dropout = 0.25                 
    batch_size = 12               
    epochs = 53
    
    model = Sequential()
    model.add(LSTM(2, input_shape=(train_x.shape[1], train_x.shape[2])))
#     model.add(Dropout(dropout))
#     model.add(LSTM(neurons, return_sequences=True, activation=activation_function))
#     model.add(Dropout(dropout))
#     model.add(LSTM(neurons, activation=activation_function))
#     model.add(Dropout(dropout))
#     model.add(Dense(units=1))
#     model.add(Activation(activation_function))
    model.compile(loss=loss, optimizer=optimizer, metrics=['mae'])
    
    model.fit(np.array(train_x),np.array(train_y),epochs=10, batch_size=5)



100%|██████████| 21805/21805 [00:00<00:00, 409323.55it/s]

BlVector==============
(21805, 2)


IndexError: tuple index out of range

In [ ]:
# company Apple
appledatas = [data for data in datas if data['company'] =='Apple Inc.']
apple_count = train_sent_dict(appledatas)
news2vector(appledatas,apple_count,bl_sent)

X1 = [data['DsVector'] for data in appledatas]
X2 = [data['SnVector'] for data in appledatas]
X3 = [data['BlVector'] for data in appledatas]
X4 = [data['PmiVector'] for data in appledatas]
# X = [data['ContextVector'] for data in datas]
X5 = [data['DsVector_rate'] for data in appledatas]

Xs = {'DsVector':X1,'SnVector':X2,'BlVector':X3,'PmiVector':X4,'DsVector_rate':X5}

Y = [np.sign(data['rate']) for data in appledatas]

for vectorname in Xs.keys():
    print(vectorname+'==============')
    X = Xs[vectorname]
    train_x,test_x,train_y,test_y = model_selection.train_test_split(X,Y,test_size=0.2,shuffle=False)

    clf = GaussianNB()
    
    clf.fit(np.array(train_x), np.array(train_y))
    predict_y = clf.predict(test_x)
    recall = recall_score(test_y,clf.predict(test_x),average = 'macro')
    precision = precision_score(test_y, clf.predict(test_x), average='macro')

    print('recall：',recall)
    print('precision：',precision)
    print('f1_score',2*recall*precision/(recall+precision))

    vote_predict_y = vote(predict_y,datas[-len(test_x):])
    vote_recall = recall_score(test_y,vote_predict_y,average = 'macro')
    vote_precision = precision_score(test_y, vote_predict_y, average='macro')

    print('voting accuracy：',accuracy(vote_predict_y,test_y))
    print('voting recall：',vote_recall)
    print('voting precision：',vote_precision)
    print('voting f1_score',2*vote_recall*vote_precision/(vote_recall+vote_precision))
    print('')

In [96]:
# company Apple Randomforest

for vectorname in Xs.keys():
    print(vectorname+'==============')
    X = Xs[vectorname]
    train_x,test_x,train_y,test_y = model_selection.train_test_split(X,Y,test_size=0.2,shuffle=False)

    clf = RandomForestClassifier(n_estimators=100, max_depth=2,random_state=0)
    
    clf.fit(np.array(train_x), np.array(train_y))
    predict_y = clf.predict(test_x)
    recall = recall_score(test_y,clf.predict(test_x),average = 'macro')
    precision = precision_score(test_y, clf.predict(test_x), average='macro')

    print('recall：',recall)
    print('precision：',precision)
    print('f1_score',2*recall*precision/(recall+precision))

    vote_predict_y = vote(predict_y,datas[-len(test_x):])
    vote_recall = recall_score(test_y,vote_predict_y,average = 'macro')
    vote_precision = precision_score(test_y, vote_predict_y, average='macro')

    print('voting accuracy：',accuracy(vote_predict_y,test_y))
    print('voting recall：',vote_recall)
    print('voting precision：',vote_precision)
    print('voting f1_score',2*vote_recall*vote_precision/(vote_recall+vote_precision))
    print('')

BlVector==============
recall： 0.49998793967470384
precision： 0.4271112946520752
f1_score 0.4606853038336461
voting


/home/stocksentiment/.local/lib/python3.5/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


voting accuracy： 0.5208952758506772
voting recall： 0.5
voting precision： 0.2604476379253386
voting f1_score 0.34249253326092854

DsVector_rate==============
recall： 0.5009265814680646
precision： 0.529247230471489
f1_score 0.5146976225543572
voting
voting accuracy： 0.5209365708622399
voting recall： 0.5001306865504281
voting precision： 0.5153190319154286
voting f1_score 0.507611271218312

SnVector==============
recall： 0.49985037680282735
precision： 0.4860512225962932
f1_score 0.4928542298913098
voting
voting accuracy： 0.5206199757735932
voting recall： 0.4997530309590441
voting precision： 0.41038596104575886
voting f1_score 0.4506819940631131

DsVector==============
recall： 0.5044502805334159
precision： 0.5429033077458991
f1_score 0.522970902968638
voting
voting accuracy： 0.5286036780090299
voting recall： 0.5084375949024605
voting precision： 0.6253113955024281
voting f1_score 0.5608504610545494

PmiVector==============
recall： 0.5061807470269806
precision： 0.5518193638132911
f1_score 0.5

In [ ]:
from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout
from keras.utils import to_categorical

Y = [np.sign(data['rate']) for data in datas]
for vectorname in Xs.keys():
    print(vectorname+'==============')
    X = Xs[vectorname]
    train_x,test_x,Y1,Y2 = model_selection.train_test_split(X,Y,test_size=0.2,shuffle=False)
    # train_x = [data['DsVector_rate'] for data in datas]
    # Y = [np.sign(data['rate']) for data in datas]
    # test_x = [data['DsVector_rate'] for data in datas2[2000:]]
    # Y2 = [np.sign(data['rate']) for data in datas2[2000:]]

    train_y = []
    for y in Y1:
        if y == 1:
            train_y.append(np.array([0,1]))
        else:    
            train_y.append(np.array([1,0]))

    test_y = []
    for y in Y2:
        if y == 1:
            test_y.append(np.array([0,1]))
        else:    
            test_y.append(np.array([1,0]))

    num_classes = 2
    model = Sequential()
    model.add(LSTM(neurons, return_sequences=True, 
    input_shape=(inputs.shape[1], inputs.shape[2]), activation=activ_func))
    model.add(Dropout(dropout))
    model.add(LSTM(neurons, return_sequences=True, activation=activ_func))
    model.add(Dropout(dropout))
    model.add(LSTM(neurons, activation=activ_func))
    model.add(Dropout(dropout))
    model.add(Dense(units=output_size))
    model.add(Activation(activ_func))
    model.compile(loss=loss, optimizer=optimizer, metrics=['mae'])
    model.summary()

In [ ]:
print(1)